In [ ]:
!pip install BERTopic

In [ ]:
!pip install bertopic
!pip install --upgrade joblib==1.1.0 # HDBScan fails to load with joblib==1.2.0
!pip install --upgrade git+https://github.com/scikit-learn-contrib/hdbscan.git#egg=hdbscan

  Using cached joblib-1.1.0-py2.py3-none-any.whl.metadata (5.2 kB)
Using cached joblib-1.1.0-py2.py3-none-any.whl (306 kB)
  Attempting uninstall: joblib
    Found existing installation: joblib 1.4.2
    Uninstalling joblib-1.4.2:
      Successfully uninstalled joblib-1.4.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
imbalanced-learn 0.12.4 requires joblib>=1.1.1, but you have joblib 1.1.0 which is incompatible.
scikit-learn 1.5.2 requires joblib>=1.2.0, but you have joblib 1.1.0 which is incompatible.
  Cloning https://github.com/scikit-learn-contrib/hdbscan.git to /tmp/pip-install-98sdbb44/hdbscan_9c1234cdec534eab91b45a0d8824d96e
  Running command git clone --filter=blob:none --quiet https://github.com/scikit-learn-contrib/hdbscan.git /tmp/pip-install-98sdbb44/hdbscan_9c1234cdec534eab91b45a0d8824d96e
  Resolved https://github.com/scikit-learn-contrib/hdbs

In [ ]:

import os
import pandas as pd
from bertopic import BERTopic
from sentence_transformers import SentenceTransformer
from sklearn.feature_extraction.text import CountVectorizer
from umap import UMAP # In case we want to make results deterministic and reproducible

In [ ]:
with open("stopwords.txt", 'r', encoding="utf8") as f:
    stop = f.read().splitlines()

vectorizer_model = CountVectorizer(ngram_range=(1, 1), stop_words=frozenset(stop))

In [ ]:
# Prepare data
df = pd.read_csv('ready_1.csv')
#df = pd.read_csv('Cov20ria.csv', encoding="cp1251")
df.head()


<ipython-input-5-8b4adfb2f390>:2: DtypeWarning: Columns (0,1,4,5) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('ready_1.csv')


Unnamed: 0 product_id                                       product_name  \
0          0    1261049  Десерт Fit Kit глазированный протеиновый Двойн...   
1          1     984168            Свеча для торта Paterra Детская Цифра 1   
2          2     984168            Свеча для торта Paterra Детская Цифра 1   
3          3     984168            Свеча для торта Paterra Детская Цифра 1   
4          4    1271460                             Сибас филе охлажденное   

   product_category product_price review_id review_author  \
0  Здоровое питание         213.0   3396923        Милана   
1  Дом, дача, книги          97.9   1977331        любовь   
2  Дом, дача, книги          97.9   1451326          инна   
3  Дом, дача, книги          97.9    449473        Marina   
4       Рыба, икра         1779.0   3444792         Роман   

                                         review_text  rating  \
0  Самое вкусное протеиновое печенье с белковым с...     5.0   
1  Веселая свечка, но нам пришла розовая, как на ...     5.0   
2                               Хорошая яркая свечка     5.0   
3  Ребенок в восторге от свечек! Она красная, кст...     5.0   
4  Хорошая рыба, вкусная, свежая. Жаль, что возят...     5.0   

                                          text_lower  \
0  самое вкусное протеиновое печенье с белковым с...   
1  веселая свечка, но нам пришла розовая, как на ...   
2                               хорошая яркая свечка   
3  ребенок в восторге от свечек! она красная, кст...   
4  хорошая рыба, вкусная, свежая. жаль, что возят...   

                                          text_punct  \
0  Самое вкусное протеиновое печенье с белковым с...   
1  Веселая свечка но нам пришла розовая как на фо...   
2                               Хорошая яркая свечка   
3  Ребенок в восторге от свечек Она красная кстат...   
4  Хорошая рыба вкусная свежая Жаль что возят без...   

                                           text_stop  \
0  Самое вкусное протеиновое печенье белковым суф...   
1  Веселая свечка нам пришла розовая фото буду ис...   
2                               Хорошая яркая свечка   
3  Ребенок восторге свечек Она красная кстати роз...   
4  Хорошая рыба вкусная свежая Жаль возят охлажда...   

                                         text_common  \
0  Самое вкусное протеиновое печенье белковым суф...   
1  Веселая свечка нам пришла розовая фото буду ис...   
2                               Хорошая яркая свечка   
3  Ребенок восторге свечек Она красная кстати роз...   
4  Хорошая рыба вкусная свежая Жаль возят охлажда...   

                                           text_rare  \
0  Самое вкусное протеиновое печенье белковым суф...   
1  Веселая свечка нам пришла розовая фото буду ис...   
2                               Хорошая яркая свечка   
3  Ребенок восторге свечек Она красная кстати роз...   
4  Хорошая рыба вкусная свежая Жаль возят охлажда...   

                                          text_nonum  \
0  Самое вкусное протеиновое печенье белковым суф...   
1  Веселая свечка нам пришла розовая фото буду ис...   
2                               Хорошая яркая свечка   
3  Ребенок восторге свечек Она красная кстати роз...   
4  Хорошая рыба вкусная свежая Жаль возят охлажда...   

                                          text_token  \
0  ['самое', 'вкусное', 'протеиновое', 'печенье',...   
1  ['веселая', 'свечка', 'нам', 'пришла', 'розова...   
2                     ['хорошая', 'яркая', 'свечка']   
3  ['ребенок', 'восторге', 'свечек', 'она', 'крас...   
4  ['хорошая', 'рыба', 'вкусная', 'свежая', 'жаль...   

                                          text_ready  
0  самый вкусный протеиновый печение белков суфле...  
1  весёлый свечка мы прийти розовый фото быть иск...  
2                               хороший яркий свечка  
3  ребёнок восторг свечка красный кстати розовый ...  
4  хороший рыба вкусный свежий жаль возить охлажд...

In [ ]:
count_row = df.shape[0]
print(count_row)

642683


In [ ]:
df = df.iloc[0:30000]

In [ ]:
docs = df['text_ready'].values.tolist()

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
from bertopic import BERTopic
import pandas as pd
import nltk
nltk.download('stopwords')
#from nltk.corpus import stopwords
from sklearn.feature_extraction.text import CountVectorizer

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [ ]:
docs

['самый вкусный протеиновый печение белков суфле весь рынок данный момент неприятный протеиновый привкус присущий подобный род изделие',
 'весёлый свечка мы прийти розовый фото быть искать далёкий нейтральный цвет единичка',
 'хороший яркий свечка',
 'ребёнок восторг свечка красный кстати розовый круто',
 'хороший рыба вкусный свежий жаль возить охлаждать лёд',
 'отличный рыба очень вкусный рекомендовать покупка',
 'отлично разделать филе кожа брать запекать кость нет рыба очень свежий',
 'очень вкусный рыба отлично упаковать',
 'рыба свежий мы совершенно понравиться',
 'свежий привозить качество высокий',
 'великолепный филе',
 'вкусный свежий упаковать жаль подорожать раз',
 'самый хороший рыба жарка',
 'рыбка понравиться соль лимон мука сковорода быстро просто маленький косточка кусок столько мой упаковка не счёт',
 'свежий очень вкусный рыба',
 'очень вкусный рыбка хорошо упаковать быстро легко готовиться',
 'супер очень свежий вкусный',
 'очень понравиться ждать филе заказывать ре

In [ ]:
from nltk.corpus import stopwords

In [ ]:
# Remove stopwords **after** generating the clusters
# NOTE: You can also perform the lemmatization here
my_stopwords = stopwords.words("russian")
vectorizer_model = CountVectorizer(stop_words=my_stopwords)

In [ ]:
#from hdbscan import HDBSCAN
documents = df['text_ready'].values.tolist()
umap_model = UMAP(n_neighbors=10, n_components=3,
                  min_dist=0.0, metric='cosine', random_state=13)   #min dist самостоятельно

In [ ]:


# Load KBLab's Swedish sentence transformer model
sentence_model = SentenceTransformer("paraphrase-multilingual-mpnet-base-v2", device="cuda")

# Initialize BERTopic with the settings we want
topic_model = BERTopic(embedding_model=sentence_model,
                       vectorizer_model=vectorizer_model,
                       umap_model=umap_model,
                       calculate_probabilities=True,
                       verbose=True)

# Fit the model
#topics, probs = topic_model.fit_transform(documents)

In [ ]:
def remove_float(documents):
  new_list = []
  for item in documents:
    if not isinstance(item, float):
      new_list.append(item)
  return new_list
#list1 = [1, 2, 3.4, 4, 5]
new_list = remove_float(documents)
print(new_list)

['самый вкусный протеиновый печение белков суфле весь рынок данный момент неприятный протеиновый привкус присущий подобный род изделие', 'весёлый свечка мы прийти розовый фото быть искать далёкий нейтральный цвет единичка', 'хороший яркий свечка', 'ребёнок восторг свечка красный кстати розовый круто', 'хороший рыба вкусный свежий жаль возить охлаждать лёд', 'отличный рыба очень вкусный рекомендовать покупка', 'отлично разделать филе кожа брать запекать кость нет рыба очень свежий', 'очень вкусный рыба отлично упаковать', 'рыба свежий мы совершенно понравиться', 'свежий привозить качество высокий', 'великолепный филе', 'вкусный свежий упаковать жаль подорожать раз', 'самый хороший рыба жарка', 'рыбка понравиться соль лимон мука сковорода быстро просто маленький косточка кусок столько мой упаковка не счёт', 'свежий очень вкусный рыба', 'очень вкусный рыбка хорошо упаковать быстро легко готовиться', 'супер очень свежий вкусный', 'очень понравиться ждать филе заказывать регулярно', 'очень 

In [ ]:
corow = len(new_list)
print(corow)

29955


In [ ]:
# Fit the model
topics, probs = topic_model.fit_transform(new_list)

2024-12-15 09:38:06,255 - BERTopic - Embedding - Transforming documents to embeddings.


Batches:   0%|          | 0/937 [00:00<?, ?it/s]

2024-12-15 09:38:45,870 - BERTopic - Embedding - Completed ✓
2024-12-15 09:38:45,873 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-12-15 09:39:43,769 - BERTopic - Dimensionality - Completed ✓
2024-12-15 09:39:43,772 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-12-15 09:50:44,899 - BERTopic - Cluster - Completed ✓
2024-12-15 09:50:44,915 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-12-15 09:50:45,621 - BERTopic - Representation - Completed ✓


In [ ]:
topic_model.get_topic_info()

Topic  Count                                            Name  \
0       -1   9249              -1_запах_брать_недостаток_упаковка   
1        0    430                0_сыр_сливочный_творожный_сырный   
2        1    422             1_шоколад_шоколадный_орех_шоколадка   
3        2    366                   2_рыба_креветка_рыбка_кальмар   
4        3    310               3_волос_шампунь_бальзам_промывать   
..     ...    ...                                             ...   
493    492     10         492_товар_доставляться_ломаться_вовремя   
494    493     10             493_хайнза_махеев_ресторий_поверить   
495    494     10             494_шляпка_недоспелва_ощипать_капец   
496    495     10  495_выдающийся_превосходный_насыщенный_ожидать   
497    496     10            496_тыква_красиво_выглядеть_красивый   

                                        Representation  \
0    [запах, брать, недостаток, упаковка, вкус, дос...   
1    [сыр, сливочный, творожный, сырный, адыгейский...   
2    [шоколад, шоколадный, орех, шоколадка, какао, ...   
3    [рыба, креветка, рыбка, кальмар, лосось, жабра...   
4    [волос, шампунь, бальзам, промывать, голова, п...   
..                                                 ...   
493  [товар, доставляться, ломаться, вовремя, обраб...   
494  [хайнза, махеев, ресторий, поверить, употребле...   
495  [шляпка, недоспелва, ощипать, капец, безвкусны...   
496  [выдающийся, превосходный, насыщенный, ожидать...   
497  [тыква, красиво, выглядеть, красивый, замечате...   

                                   Representative_Docs  
0    [удобно покупать больший упаковка цена, достои...  
1    [очень вкусный сыр, очень вкусный сыр, сыр вку...  
2    [вкусный шоколад, вкусный шоколад, вкусный шок...  
3    [свежий очень вкусный рыба, вкусный очень свеж...  
4    [достоинство хороший шампунь, отличный шампунь...  
..                                                 ...  
493  [свежий товар, ломаться обработка судить красн...  
494  [достоинство удобно вкусно быстро недостаток ж...  
495  [твёрдый недоспелва безвкусный, ужасно твёрдый...  
496  [достоинство насыщенный вкус, достоинство прев...  
497  [очень вкусный тыква, очень вкусный тыква, оче...  

[498 rows x 5 columns]

In [ ]:
topic_model.get_topic(0)

[('сыр', 0.0612774828195227),
 ('сливочный', 0.012640817163575156),
 ('творожный', 0.011977516535355604),
 ('сырный', 0.011255759032950204),
 ('адыгейский', 0.010128391656952162),
 ('плавленый', 0.008837284681765992),
 ('полутвёрдый', 0.008150251117819612),
 ('пресный', 0.006891007315209514),
 ('солёный', 0.006823938272531598),
 ('плавить', 0.006589612211457099)]

In [ ]:
topic_model.get_representative_docs(0)

['очень вкусный сыр', 'очень вкусный сыр', 'сыр вкусный']

In [ ]:
topic_model.get_topic(1) # topic_model.get_topic(similar_topics[0])

[('шоколад', 0.05765928089177191),
 ('шоколадный', 0.02827786373257985),
 ('орех', 0.020773850397802045),
 ('шоколадка', 0.020379043177270045),
 ('какао', 0.017765366851059176),
 ('молочный', 0.015724949955120863),
 ('глазурь', 0.01327435425754611),
 ('фундук', 0.010828536109811833),
 ('цельный', 0.010191418888639097),
 ('орешек', 0.00978205848716411)]

In [ ]:
topic_model.visualize_topics()

In [ ]:
fig = topic_model.visualize_topics()
fig.write_html("/content/sample_data/ria_topic_20t.html")

In [ ]:
topic_model.visualize_hierarchy()

In [ ]:
print(len(docs), len(range(len(docs))), len(topics))

30000 30000 29955


In [ ]:
docs = docs[:-45]


In [ ]:
print(len(documents))

30000


In [ ]:
documents = documents[:-45]

In [ ]:
hierarchical_topics = topic_model.hierarchical_topics(new_list)
topic_model.visualize_hierarchy(hierarchical_topics=hierarchical_topics)

100%|██████████| 496/496 [00:03<00:00, 138.05it/s]


In [ ]:
documents

['самый вкусный протеиновый печение белков суфле весь рынок данный момент неприятный протеиновый привкус присущий подобный род изделие',
 'весёлый свечка мы прийти розовый фото быть искать далёкий нейтральный цвет единичка',
 'хороший яркий свечка',
 'ребёнок восторг свечка красный кстати розовый круто',
 'хороший рыба вкусный свежий жаль возить охлаждать лёд',
 'отличный рыба очень вкусный рекомендовать покупка',
 'отлично разделать филе кожа брать запекать кость нет рыба очень свежий',
 'очень вкусный рыба отлично упаковать',
 'рыба свежий мы совершенно понравиться',
 'свежий привозить качество высокий',
 'великолепный филе',
 'вкусный свежий упаковать жаль подорожать раз',
 'самый хороший рыба жарка',
 'рыбка понравиться соль лимон мука сковорода быстро просто маленький косточка кусок столько мой упаковка не счёт',
 'свежий очень вкусный рыба',
 'очень вкусный рыбка хорошо упаковать быстро легко готовиться',
 'супер очень свежий вкусный',
 'очень понравиться ждать филе заказывать ре

In [ ]:
def remove_float(docs):
  new_doc = []
  for item in docs:
    if not isinstance(item, float):
      new_doc.append(item)
  return new_doc
#list1 = [1, 2, 3.4, 4, 5]
new_doc = remove_float(docs)
print(new_doc)

['самый вкусный протеиновый печение белков суфле весь рынок данный момент неприятный протеиновый привкус присущий подобный род изделие', 'весёлый свечка мы прийти розовый фото быть искать далёкий нейтральный цвет единичка', 'хороший яркий свечка', 'ребёнок восторг свечка красный кстати розовый круто', 'хороший рыба вкусный свежий жаль возить охлаждать лёд', 'отличный рыба очень вкусный рекомендовать покупка', 'отлично разделать филе кожа брать запекать кость нет рыба очень свежий', 'очень вкусный рыба отлично упаковать', 'рыба свежий мы совершенно понравиться', 'свежий привозить качество высокий', 'великолепный филе', 'вкусный свежий упаковать жаль подорожать раз', 'самый хороший рыба жарка', 'рыбка понравиться соль лимон мука сковорода быстро просто маленький косточка кусок столько мой упаковка не счёт', 'свежий очень вкусный рыба', 'очень вкусный рыбка хорошо упаковать быстро легко готовиться', 'супер очень свежий вкусный', 'очень понравиться ждать филе заказывать регулярно', 'очень 

In [ ]:
print(len(new_list))

29955


In [ ]:
topic_model.reduce_topics(new_list, nr_topics=20)

2024-12-15 09:56:29,977 - BERTopic - Topic reduction - Reducing number of topics
2024-12-15 09:56:30,332 - BERTopic - Topic reduction - Reduced number of topics from 100 to 20


In [ ]:
topic_model.get_topic_info()

Topic  Count                                      Name  \
0      -1   9249         -1_очень_достоинство_хороший_вкус   
1       0  11466              0_вкусный_очень_хороший_вкус   
2       1   2699      1_свежий_достоинство_хороший_спасибо   
3       2   2351                      2_вода_чай_кофе_вкус   
4       3    949                 3_волос_кожа_крем_капсула   
5       4    899             4_качество_цена_товар_хороший   
6       5    679        5_салфетка_упаковка_удобный_размер   
7       6    586         6_ребёнок_детство_нравиться_семья   
8       7    376             7_кошка_корм_кот_удовольствие   
9       8    317         8_подгузник_малыш_ребёнок_pampers   
10      9     87                  9_зуб_зубной_щётка_паста   
11     10     70        10_нормальный_норма_уксус_окорочка   
12     11     53             11_дорого_цена_дороговатый_95   
13     12     46             12_рис_рисовый_добавить_лапша   
14     13     37   13_витамин_витаминный_витаминк_комплекс   
15     14     35                 14_сон_ночью_комфорт_ночь   
16     15     17         15_посуда_fairy_platinum_средство   
17     16     15         16_яйцо_яичница_коричневый_размер   
18     17     13   17_идеальный_идеально_эрлгреть_причтной   
19     18     11  18_натуральный_продукт_признак_природный   

                                       Representation  \
0   [очень, достоинство, хороший, вкус, вкусный, н...   
1   [вкусный, очень, хороший, вкус, отличный, вкус...   
2   [свежий, достоинство, хороший, спасибо, очень,...   
3   [вода, чай, кофе, вкус, достоинство, пить, хор...   
4   [волос, кожа, крем, капсула, шампунь, средство...   
5   [качество, цена, товар, хороший, отличный, про...   
6   [салфетка, упаковка, удобный, размер, кг, бума...   
7   [ребёнок, детство, нравиться, семья, удовольст...   
8   [кошка, корм, кот, удовольствие, собака, нрави...   
9   [подгузник, малыш, ребёнок, pampers, premium, ...   
10  [зуб, зубной, щётка, паста, чистка, чистить, э...   
11  [нормальный, норма, уксус, окорочка, кисловаты...   
12  [дорого, цена, дороговатый, 95, дорога, 11, до...   
13  [рис, рисовый, добавить, лапша, пшеничный, гот...   
14  [витамин, витаминный, витаминк, комплекс, овощ...   
15  [сон, ночью, комфорт, ночь, день, прокладка, з...   
16  [посуда, fairy, platinum, средство, мытьё, арб...   
17  [яйцо, яичница, коричневый, размер, небитый, к...   
18  [идеальный, идеально, эрлгреть, причтной, смуз...   
19  [натуральный, продукт, признак, природный, вся...   

                                  Representative_Docs  
0   [достоинство самый любимый соус очень вкусный ...  
1       [очень вкусный, очень вкусный, очень вкусный]  
2   [хороший свежий, хороший свежий, достоинство о...  
3   [хороший вкусный вода, хороший вкусный вода, х...  
4   [натуральный лёгкий крем нежный кожа вокруг гл...  
5   [цена качество отличный, хороший качество цена...  
6   [хороший удобный упаковка, достоинство удобный...  
7   [вкусный ребёнок есть, вкусный ребёнок нравить...  
8   [очень хороший корм кошка есть удовольствие, х...  
9   [отличный подгузник мы очень подойти пробовать...  
10  [чистить зубной паста, ребёнок щётка сразу пон...  
11               [нормальный, нормальный, нормальный]  
12              [дорого, хорошо дорого, очень дорого]  
13  [хороший рис, очень вкусный рис, очень вкусный...  
14   [хороший витамин, хороший витамин, один витамин]  
15  [отличный продукт устраивать абсолютно всё раз...  
16  [обожать средство мытьё посуда fairy platinum ...  
17  [яйцо крупный коричневый, хороший вкусный яйцо...  
18                  [идеальный, идеальный, идеальный]  
19            [натуральный, натуральный, натуральный]

In [ ]:
topic_model.get_topic(3)

[('волос', 0.06404444629213561),
 ('кожа', 0.049337244664235134),
 ('крем', 0.041810116682132054),
 ('капсула', 0.036966305004129764),
 ('шампунь', 0.035583954152941064),
 ('средство', 0.03247285372417108),
 ('стирка', 0.03221801155789139),
 ('мыло', 0.021312017297152642),
 ('запах', 0.021069031104341693),
 ('глаз', 0.02064744922741358)]

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_barchart(width=280, height=330,top_n_topics=20, n_words=20)

In [ ]:
fig4 = topic_model.visualize_barchart(width=280, height=330,top_n_topics=20, n_words=20)
fig4.write_html("/content/sample_data/ria_topic_20wordBars.html")

In [ ]:
topic_model.visualize_heatmap(n_clusters=9)

In [ ]:
fig5 = topic_model.visualize_heatmap(n_clusters=9)
fig5.write_html("/content/sample_data/ria_topic_20corr.html")